# Sentiment analysis using pre-trained language models

## Download Hugging face lib

https://huggingface.co/docs/transformers/v4.15.0/installation

In [2]:
import json
!conda install -c huggingface transformers
!pip install torch 
!pip install chardet

'conda' is not recognized as an internal or external command,
operable program or batch file.


In [64]:
from transformers import pipeline

classifier = pipeline("sentiment-analysis")

# classifier_amazon("This is horrible")

No model was supplied, defaulted to distilbert-base-uncased-finetuned-sst-2-english and revision af0f99b (https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english).
Using a pipeline without specifying a model name and revision in production is not recommended.


[{'label': 'POSITIVE', 'score': 0.9994421601295471}]

In [53]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoModelForSequenceClassification.from_pretrained("LiYuan/amazon-review-sentiment-analysis")
tokenizer.predict("I am impressed how long this ink last and how fast the seller sent it to me. Not a hitch at all, fantastic.")

AttributeError: 'BertForSequenceClassification' object has no attribute 'predict'

In [69]:
import regex as re

def preprocess_input(review_param):
    # Remove punctuation
    review_p = "".join(char for char in review_param if char not in string.punctuation)
    # Only get characters
    review_sub = re.sub(r"[^-/().&' \w]|_", "", review_p)
    # Replace all whitespace with space
    review_sub = re.sub(r"\s", " ", review_sub)
    # Replace multiple spaces with one space
    review_sub = re.sub(r"  ", " ", review_sub)
    print(review_sub)
    return review_sub[:450]
    # print(review_sub)

s = "To  start off my hand size is 17x10 cm so I have \u201cmedium\u201d sized hands and the difference between this and the viper ultimate was night and day for me. The sensor felt really nice and my first time using it I broke all my Kovaaks and sim labs records. I used a fingertip grip mostly but sometimes claw and it perfect for both. If you use a palm grip you will need very small hands for that. I can Palm it just a little bit. I\u2019ve never had my sim in games feel so familiar. I\u2019ve used the pulsefire haste, Aeros 3 wireless (2022), the razer viper ultimate, and the deathadder v2 pro and this is just the best mouse I have ever used. The sensor implementation feels very nice and the side buttons are very nice and clicks (a huge problem on the razer viper ultimate) the feet feel amazing. I think this is my endgame I couldn\u2019t recommend it more."

print(preprocess_input(s))
classifier(preprocess_input(s))

To start off my hand size is 17x10 cm so I have medium sized hands and the difference between this and the viper ultimate was night and day for me The sensor felt really nice and my first time using it I broke all my Kovaaks and sim labs records I used a fingertip grip mostly but sometimes claw and it perfect for both If you use a palm grip you will need very small hands for that I can Palm it just a little bit Ive never had my sim in games feel so familiar Ive used the pulsefire haste Aeros 3 wireless 2022 the razer viper ultimate and the deathadder v2 pro and this is just the best mouse I have ever used The sensor implementation feels very nice and the side buttons are very nice and clicks a huge problem on the razer viper ultimate the feet feel amazing I think this is my endgame I couldnt recommend it more
To start off my hand size is 17x10 cm so I have medium sized hands and the difference between this and the viper ultimate was night and day for me The sensor felt really nice and 

[{'label': 'POSITIVE', 'score': 0.989682674407959}]

In [ ]:
def score_to_stars(sentiment_score):
    if sentiment_score < 0.2:
        return 1
    elif sentiment_score < 0.4:
        return 2
    elif sentiment_score < 0.6:
        return 3
    elif sentiment_score <0.8:
        return 4
    return 5

In [70]:
import json
import string
import re
import numpy as np
with open('reviews_final_extracted.json') as f:
    reviews = json.load(f)
# print(json.dumps(reviews, indent=2))

sentiment_dict = dict()
for brand in reviews:
    brand_dict = dict()
    for category in reviews[brand]:
        category_list = []
        for product in reviews[brand][category]:
            product_dict = dict()
            sentiment_model_dict = dict()
            sentiment_list = []
            # star_list = []
            for review in product["reviews"]:
                if len(review) > 0:
                    review_sub = preprocess_input(review)
                    # try:
                    results = classifier(review_sub)[0]
                    print(results)
                    # score = results['score']
                    label = results['label']
                    if label == 'NEGATIVE':
                        sentiment_list.append(0)
                    else:
                        sentiment_list.append(1)
                        # star_list.append(score_to_stars(score))
                    # except Exception as e:
                    #     print(e)
            sentiment_model_dict["model"] = "distilbert-base-uncased-finetuned-sst-2-english"
            sentiment_model_dict["sentiment"] = np.mean(sentiment_list)
            # sentiment_model_dict["star"] = np.mean(star_list)
            product_dict["name"] = product["name"]
            product_dict["rating"] = product["rating"]
            product_dict["sentiment"] = sentiment_model_dict
            category_list.append(product_dict)
        brand_dict[category] = category_list
    sentiment_dict[brand] = brand_dict

print(sentiment_dict)
with open('reviews_sentiment_final_base_extracted.json', 'w') as f:
    json.dump(sentiment_dict, f, indent=2)

The Razer Arochi V2 is a great performer and looks nice with other white accessories I picked this one up for my ASUS G14 and it has worked flawlessly The build quality responsiveness and battery life are superb I also have a Razer Basilisk X Hyperspeed that I use with my main desktop and the Arochi keeps up with it in terms of performance The only complaint I have is my own fault as I have bigger hands and the Arochi V2 is on the more compact size of mice so it can get uncomfortable for extended use periods
{'label': 'POSITIVE', 'score': 0.9988486766815186}
More like like new than buy new Maybe its the lack of care in the Amazon warehouse since its been shipped from there The packaging was ripped the seal sticker looked opened and the mouse padding at the bottom wasdirty Is this item presentable to gift Not really Is it still functional Yeah at least as of right now day 1 of recieving the itemIts not ergonomic to me But I have small handsthat the mouse is perfect fitThe latency is min

In [71]:
classifier_amazon = pipeline("sentiment-analysis", model="LiYuan/amazon-review-sentiment-analysis")
classifier_amazon("To  start off my hand size is 17x10 cm so I have \u201cmedium\u201d sized hands and the difference between this and the viper ultimate was night and day for me. The sensor felt really nice and my first time using it I broke all my Kovaaks and sim labs records. I used a fingertip grip mostly but sometimes claw and it perfect for both. If you use a palm grip you will need very small hands for that. I can Palm it just a little bit. I\u2019ve never had my sim in games feel so familiar. I\u2019ve used the pulsefire haste, Aeros 3 wireless (2022), the razer viper ultimate, and the deathadder v2 pro and this is just the best mouse I have ever used. The sensor implementation feels very nice and the side buttons are very nice and clicks (a huge problem on the razer viper ultimate) the feet feel amazing. I think this is my endgame I couldn\u2019t recommend it more.")

[{'label': '5 stars', 'score': 0.5687509775161743}]

In [72]:
classifier_amazon = pipeline("sentiment-analysis", model="LiYuan/amazon-review-sentiment-analysis")

with open('reviews_final_extracted.json') as f:
    reviews = json.load(f)
# print(json.dumps(reviews, indent=2))

sentiment_dict = dict()
for brand in reviews:
    brand_dict = dict()
    for category in reviews[brand]:
        category_list = []
        for product in reviews[brand][category]:
            product_dict = dict()
            sentiment_model_dict = dict()
            sentiment_list = []
            # star_list = []
            for review in product["reviews"]:
                if len(review) > 0:
                    review_sub = preprocess_input(review)
                    results = classifier_amazon(review_sub)[0]
                    print(results)
                    # score = results['score']
                    label = results['label']
                    score = int(label.split(' ')[0])
                    sentiment_list.append(score)
            sentiment_model_dict["model"] = "LiYuan/amazon-review-sentiment-analysis"
            sentiment_model_dict["sentiment"] = np.mean(sentiment_list)
            # sentiment_model_dict["star"] = np.mean(star_list)
            product_dict["name"] = product["name"]
            product_dict["rating"] = product["rating"]
            product_dict["sentiment"] = sentiment_model_dict
            category_list.append(product_dict)
        brand_dict[category] = category_list
    sentiment_dict[brand] = brand_dict

print(sentiment_dict)
with open('reviews_sentiment_final_liyuan_extracted.json', 'w') as f:
    json.dump(sentiment_dict, f, indent=2)

The Razer Arochi V2 is a great performer and looks nice with other white accessories I picked this one up for my ASUS G14 and it has worked flawlessly The build quality responsiveness and battery life are superb I also have a Razer Basilisk X Hyperspeed that I use with my main desktop and the Arochi keeps up with it in terms of performance The only complaint I have is my own fault as I have bigger hands and the Arochi V2 is on the more compact size of mice so it can get uncomfortable for extended use periods
{'label': '5 stars', 'score': 0.49709728360176086}
More like like new than buy new Maybe its the lack of care in the Amazon warehouse since its been shipped from there The packaging was ripped the seal sticker looked opened and the mouse padding at the bottom wasdirty Is this item presentable to gift Not really Is it still functional Yeah at least as of right now day 1 of recieving the itemIts not ergonomic to me But I have small handsthat the mouse is perfect fitThe latency is min